# Multi-Object Optimization

This notebook allows the identification of paths that balance multiple objectives, e.g., distance, comfort, safety, for pedestrians and cyclists.

The graphs used are created using Neo4j through the code in the GitHub repository: [https://github.com/federicarollo/GRAFMOVE](https://github.com/federicarollo/GRAFMOVE).

Then, each graph was extracted as a collection of two CSV files, available in the **[data folder](https://github.com/federicarollo/ITADATA25/data)**, using the following Cypher queries:

- `MATCH (n) RETURN id(n) AS id, labels(n) AS labels, apoc.convert.toJson(properties(n)) AS properties` for nodes
- `MATCH (n)-[r]->(m) RETURN id(n) as source, id(m) as target, type(r) as type, apoc.convert.toJson(properties(r)) as properties` for edges

The graph structure follows the OpenStreetMap (OSM) structure:
- **Nodes** represent OSM-defined junctions or road shape points, mantaining the OSM identifier and the GPS coordinates as properties,
- **Edges** correspond to roads, with properties that describe their shape, length, type. The direction of the edge indicates the permitted travel direction.

<img src="https://raw.githubusercontent.com/federicarollo/ITADATA25/main/data/images/osm_structure_and_green.png" style="display: block; margin-left: auto; margin-right: auto;" alt="OSM structure" width="700"/>


<div>
  <br><br>    
  <p style="float: left; width: 50%;">
    <b>FootNodes</b> represent nodes where pedestrian access is allowed, whereas <b>BikeNodes</b> correspond to nodes for cyclists.<br>ROUTE edges represent the roads.<br><br>The graph is enriched by the localization of the Point Of Interests (POIs) represented by the <b>POI</b> nodes, and linked to the corresponding elements in OSM (<b>OSMNode</b> or <b>OSMWay</b> if they are stored in OSM as node or way, respectively). The <b>Tag</b> nodes store the characteristics of the POIs (e.g., name, type such touristic attraction or parking).
  </p>
  <img src="https://raw.githubusercontent.com/federicarollo/ITADATA25/main/data/images/graph structure.png" style="display: block; margin-left: auto; margin-right: auto;" alt="Graph structure" style="float: right; width: 40%;">
</div>
<div style="clear: both;"></div>

## Configuration parameters

In [1]:
nodes_filename = "../data/graphs/Ferrara/ferrara_nodes.csv"
edges_filename = "../data/graphs/Ferrara/ferrara_edges.csv"

## Import libraries

In [14]:
!pip install folium

  Using cached folium-0.20.0-py2.py3-none-any.whl.metadata (4.2 kB)
  Using cached branca-0.8.1-py3-none-any.whl.metadata (1.5 kB)
Using cached folium-0.20.0-py2.py3-none-any.whl (113 kB)
Using cached branca-0.8.1-py3-none-any.whl (26 kB)

   ------------- -------------------------- 1/3 [branca]
   -------------------------- ------------- 2/3 [folium]
   -------------------------- ------------- 2/3 [folium]
   -------------------------- ------------- 2/3 [folium]
   -------------------------- ------------- 2/3 [folium]
   -------------------------- ------------- 2/3 [folium]
   -------------------------- ------------- 2/3 [folium]
   -------------------------- ------------- 2/3 [folium]
   ---------------------------------------- 3/3 [folium]



In [12]:
!pip install torch_geometric

  Using cached torch_geometric-2.6.1-py3-none-any.whl.metadata (63 kB)
Using cached torch_geometric-2.6.1-py3-none-any.whl (1.1 MB)

   ----------------------------------------  0/10 [tqdm]
   ----------------------------------------  0/10 [tqdm]
   ----------------------------------------  0/10 [tqdm]
   ----------------------------------------  0/10 [tqdm]
   ---- -----------------------------------  1/10 [propcache]
   ------------ ---------------------------  3/10 [frozenlist]
   -------------------- -------------------  5/10 [aiohappyeyeballs]
   ------------------------ ---------------  6/10 [yarl]
   -------------------------------- -------  8/10 [aiohttp]
   -------------------------------- -------  8/10 [aiohttp]
   -------------------------------- -------  8/10 [aiohttp]
   -------------------------------- -------  8/10 [aiohttp]
   -------------------------------- -------  8/10 [aiohttp]
   -------------------------------- -------  8/10 [aiohttp]
   -------------------------

In [3]:
# !pip install pymoo

In [4]:
# pip install folium

In [10]:
!pip3 install torch torchvision

  Using cached sympy-1.14.0-py3-none-any.whl.metadata (12 kB)
   ---------------------------------------- 0.0/241.4 MB ? eta -:--:--
   ---------------------------------------- 0.0/241.4 MB ? eta -:--:--
   ---------------------------------------- 0.3/241.4 MB ? eta -:--:--
   ---------------------------------------- 0.5/241.4 MB 989.2 kB/s eta 0:04:04
   ---------------------------------------- 0.8/241.4 MB 960.2 kB/s eta 0:04:11
   ---------------------------------------- 1.0/241.4 MB 1.1 MB/s eta 0:03:45
   ---------------------------------------- 1.0/241.4 MB 1.1 MB/s eta 0:03:45
   ---------------------------------------- 1.3/241.4 MB 1.1 MB/s eta 0:03:46
   ---------------------------------------- 1.6/241.4 MB 1.1 MB/s eta 0:03:43
   ---------------------------------------- 1.8/241.4 MB 1.1 MB/s eta 0:03:44
   ---------------------------------------- 2.1/241.4 MB 1.1 MB/s eta 0:03:45
   ---------------------------------------- 2.1/241.4 MB 1.1 MB/s eta 0:03:45
   ----------------

In [6]:
# !pip install networkx

   ---------------------------------------- 0.0/1.7 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.7 MB ? eta -:--:--
   ------ --------------------------------- 0.3/1.7 MB ? eta -:--:--
   ------------ --------------------------- 0.5/1.7 MB 1.4 MB/s eta 0:00:01
   ------------------ --------------------- 0.8/1.7 MB 1.1 MB/s eta 0:00:01
   ------------------------ --------------- 1.0/1.7 MB 986.7 kB/s eta 0:00:01
   ------------------------ --------------- 1.0/1.7 MB 986.7 kB/s eta 0:00:01
   ------------------------------ --------- 1.3/1.7 MB 986.4 kB/s eta 0:00:01
   ---------------------------------------- 1.7/1.7 MB 1.1 MB/s  0:00:01


In [8]:
# !pip install pandas

  Using cached pytz-2025.2-py2.py3-none-any.whl.metadata (22 kB)
   ---------------------------------------- 0.0/11.3 MB ? eta -:--:--
   ---------------------------------------- 0.0/11.3 MB ? eta -:--:--
    --------------------------------------- 0.3/11.3 MB ? eta -:--:--
   - -------------------------------------- 0.5/11.3 MB 932.9 kB/s eta 0:00:12
   - -------------------------------------- 0.5/11.3 MB 932.9 kB/s eta 0:00:12
   - -------------------------------------- 0.5/11.3 MB 932.9 kB/s eta 0:00:12
   - -------------------------------------- 0.5/11.3 MB 932.9 kB/s eta 0:00:12
   -- ------------------------------------- 0.8/11.3 MB 532.8 kB/s eta 0:00:20
   -- ------------------------------------- 0.8/11.3 MB 532.8 kB/s eta 0:00:20
   -- ------------------------------------- 0.8/11.3 MB 532.8 kB/s eta 0:00:20
   --- ------------------------------------ 1.0/11.3 MB 466.2 kB/s eta 0:00:23
   ---- ----------------------------------- 1.3/11.3 MB 528.5 kB/s eta 0:00:19
   ----- -----

In [15]:
import networkx as nx
import numpy as np
import pandas as pd
import json
# from itertools import combinations, islice, product, combinations_with_replacement

import torch
import torch.nn.functional as F
from torch_geometric.nn import GCNConv
from torch_geometric.data import Data

from pymoo.core.problem import Problem
from pymoo.algorithms.moo.nsga2 import NSGA2
from pymoo.optimize import minimize
from pymoo.indicators.hv import HV
from pymoo.visualization.scatter import Scatter
from pymoo.termination.default import DefaultMultiObjectiveTermination

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

import folium as fo

In [16]:
def double_unescape_json(s):
    unescaped = s.encode('utf-8').decode('unicode_escape')
    return json.loads(unescaped)

## Step 1 – Graph Import

In [17]:
nodes_df = pd.read_csv(nodes_filename)
edges_df = pd.read_csv(edges_filename)

In [18]:
nodes_df.shape

(55026, 3)

### Time-dependent properties vs time invariant properties

In [19]:
edges_df['properties'][233]

'{\\"foot_class\\":2,\\"distance\\":8.629131689296166,\\"green_area\\":0,\\"green_area_weight\\":8.629131689296166,\\"length\\":\\"8.619483996069556\\",\\"oneway\\":\\"False\\",\\"pm25\\":[17.964931417986364,35.213726853722704,22.390966066730627,20.3181468360084],\\"name\\":\\"Rampari di San Paolo\\",\\"geometry\\":\\"LINESTRING(11.6141052 44.8330706, 11.6141774 44.8330124)\\",\\"highway\\":\\"residential\\",\\"bike_class\\":2,\\"reversed\\":\\"True\\",\\"pm25_per_meter\\":[155.02175899497843,303.86388629167794,193.21459484038039,175.3279647303727]}'

In [20]:
double_unescape_json(edges_df['properties'][233])

{'foot_class': 2,
 'distance': 8.629131689296166,
 'green_area': 0,
 'green_area_weight': 8.629131689296166,
 'length': '8.619483996069556',
 'oneway': 'False',
 'pm25': [17.964931417986364,
  35.213726853722704,
  22.390966066730627,
  20.3181468360084],
 'name': 'Rampari di San Paolo',
 'geometry': 'LINESTRING(11.6141052 44.8330706, 11.6141774 44.8330124)',
 'highway': 'residential',
 'bike_class': 2,
 'reversed': 'True',
 'pm25_per_meter': [155.02175899497843,
  303.86388629167794,
  193.21459484038039,
  175.3279647303727]}

In [21]:
double_unescape_json(edges_df['properties'][233])['distance']

8.629131689296166

In [22]:
double_unescape_json(edges_df['properties'][233])['pm25']

[17.964931417986364, 35.213726853722704, 22.390966066730627, 20.3181468360084]

### Load the graph

In [23]:
%%time

G = nx.DiGraph()

for _, row in nodes_df.iterrows():
    properties = double_unescape_json(row['properties'])
    G.add_node(row['id'], labels=row['labels'], **properties)

for _, row in edges_df.iterrows():
    properties = double_unescape_json(row['properties'])
    G.add_edge(row['source'], row['target'], label=row['type'], **properties)

CPU times: total: 22.4 s
Wall time: 23.2 s


In [24]:
print(f"Nodes: {len(G.nodes())}, Edges: {len(G.edges())}")

Nodes: 55026, Edges: 141480


### What are the properties of the FootNode instances?

In [25]:
node_properties = set()

for _, data in G.nodes(data=True):
    if 'FootNode' in data.get('labels', []):
        # Aggiungi tutte le chiavi tranne 'labels'
        node_properties.update(k for k in data.keys() if k != 'labels')

print(f"Properties of FootNode instances: {node_properties}")

Properties of FootNode instances: {'id', 'railway', 'longitude', 'bbox', 'highway', 'x', 'y', 'cyclist_allowed_grafmove', 'location', 'componentId', 'latitude', 'green_area', 'lat', 'geometry', 'street_count', 'pedestrian_allowed_grafmove', 'gtype', 'lon'}


### What are the properties of the ROUTE edge instances?

In [26]:
edge_property = set()

for u, v, data in G.edges(data=True):
    if data.get('label') == 'ROUTE':
        edge_property.update(k for k in data.keys() if k != 'labels')

print(f"Properties of ROUTE instances: {edge_property}")

Properties of ROUTE instances: {'oneway', 'foot_class', 'distance', 'bike_class', 'created_date', 'green_area_weight', 'ref', 'created_with', 'lanes', 'highway', 'crs', 'junction', 'pm25_per_meter', 'area', 'maxspeed', 'pm25', 'name', 'bridge', 'service', 'width', 'tunnel', 'length', 'green_area', 'geometry', 'reversed', 'access', 'label'}


### What are all the possible values of the *highway* property of ROUTE?

In [27]:
highway_values = set()

for _, _, data in G.edges(data=True):
    if data.get('label') == 'ROUTE' and 'highway' in data:
        highway_values.add(data['highway'])

print(highway_values)

{'motorway_link', 'living_street', 'trunk', 'track', 'trunk_link', 'road', 'motorway', 'pedestrian', 'tertiary', 'services', 'secondary', 'bridleway', 'path', 'steps', 'primary_link', 'tertiary_link', 'cycleway', 'unclassified', 'service', 'residential', 'footway', 'primary'}


### Road length values

In [28]:
route_distances = [
    data['distance']
    for u, v, data in G.edges(data=True)
    if data.get('type') == 'ROUTE' and 'distance' in data
]

In [ ]:
plt.boxplot(route_distances)
plt.title("Boxplot of Route Distances")
plt.ylabel("Distance")
plt.grid(True)
plt.show()

In [1]:
import matplotlib; print(matplotlib.__version__)

3.10.6


## Step 2 - Path generation

### Configuration parameters

In [47]:
OBJS_NOTIME = ["distance", "green_area_weight"]
OBJS_TIME = ["pm25_per_meter"] #["crash_risk_density_norm"]
TIME_INTERVAL = 0 # one of the following values: {NIGHT: 0, MORNING: 1, AFTERNOON: 2, EVENING: 3}

N_OBJS = len(OBJS_NOTIME+OBJS_TIME)

N_CANDIDATE_PATHS = 1000

### Subgraph definition: pedestrians or cyclists?

In [57]:
%%time

foot_nodes = [
    n for n, data in G.nodes(data=True)
    if "labels" in data and "FootNode" in data["labels"]
]

route_edges = [
    (u, v) for u, v, data in G.edges(data=True)
    if "label" in data and data["label"] == "ROUTE"
    and u in foot_nodes and v in foot_nodes
]

H = G.edge_subgraph(route_edges).copy()

In [58]:
print(f"Nodes: {len(H.nodes())}, Edges: {len(H.edges())}")

Nodes: 34661, Edges: 67296


The *get_candidate_paths* function takes as input:
- the graph H
- the OpenstreetMap identifiers (as string) of the source and target nodes (these nodes can be visualized in OSM by replacing the identifier in a link like https://www.openstreetmap.org/node/2093992765)
- the number of paths to generate (optional)

and provides as output a set of *num_paths* paths between source and target

In [61]:
def get_candidate_paths(G, source, target, num_paths=10):
    paths = []
    
    for node, data in G.nodes(data=True):
        if 'FootNode' in data.get('labels', []) and str(data.get("id")) == source:
            source_node = node
            print("Source node found:", node)
            break
    else:
        print("Source node not found.")

    for node, data in G.nodes(data=True):
        if 'FootNode' in data.get('labels', []) and str(data.get("id")) == target:
            target_node = node
            print("Target node found:", node)
            break
    else:
        print("Target node not found.")
    
    for obj in OBJS_NOTIME:
        paths.append(nx.shortest_path(G, source_node, target_node, weight=obj))
    for obj in OBJS_TIME:
        paths.append(nx.shortest_path(G, source_node, target_node, weight=obj[TIME_INTERVAL]))
    for _ in range(num_paths - N_OBJS):
        random_path = nx.shortest_path(G, source_node, target_node, weight=lambda u, v, d: torch.rand(1).item())
        paths.append(random_path)
        
    return paths

Choose one of these exemplar origin-destination points:

In [71]:
%%time


# ---------- FERRARA ---------- 
s, t = "1150817556", "2093992765"
# s, t ="2711436174", "2093992765"
# s, t ="958004696", "259040297"
# s, t ="2211349960", "1836899403"


# ---------- MODENA ---------- 
# s, t ="10053840073", "2041913868"
# s, t ="250846426", "256411970"
# s, t ="250850846", "2021402066"


paths = get_candidate_paths(H, source=s, target=t, num_paths=N_CANDIDATE_PATHS)

Source node found: 3925
Target node found: 15052
CPU times: total: 7min 35s
Wall time: 8min 20s


In [72]:
print(f"Number of paths: {len(paths)}")

Number of paths: 1000


In [73]:
no_duplicates = []

for element in paths:
    if(element not in no_duplicates):
        no_duplicates.append(element)

In [74]:
print(f"Number of non duplicated paths: {len(no_duplicates)}")

Number of non duplicated paths: 962


In [75]:
def evaluate_path(G, path):
    eval_objs = {}

    for obj in OBJS_NOTIME:
        eval_objs[obj] = 0
    for obj in OBJS_TIME:
        eval_objs[obj] = 0

    for i in range(len(path)-1):
        u, v = path[i], path[i+1]
        
        for obj in OBJS_NOTIME:
            eval_objs[obj] += G.edges[u, v][obj]
        for obj in OBJS_TIME:
            value = float(G.edges[u, v][obj][0])
            eval_objs[obj] += value
        
    return eval_objs

path_data = []
for path in no_duplicates:
    eval_objs = evaluate_path(H, path)
    eval_objs["path"] = path
    path_data.append(eval_objs)

In [76]:
print(f"Number of evaluated paths: {len(path_data)}")

Number of evaluated paths: 962


In [77]:
path_data

[{'distance': 4532.129193757298,
  'green_area_weight': 3571.106561508193,
  'pm25_per_meter': 74479.29008014814,
  'path': [3925,
   3911,
   2912,
   2955,
   2919,
   2971,
   26215,
   26217,
   8506,
   8503,
   8502,
   8504,
   26218,
   26216,
   8500,
   8501,
   8505,
   12445,
   12431,
   12436,
   17633,
   12439,
   12437,
   12407,
   12440,
   12450,
   34468,
   34456,
   34478,
   34475,
   34470,
   34469,
   34473,
   34481,
   34459,
   34458,
   34471,
   34462,
   34455,
   34465,
   34454,
   34466,
   34476,
   34482,
   34467,
   34461,
   34480,
   34483,
   34486,
   34463,
   38212,
   38211,
   38210,
   38209,
   38208,
   38207,
   38206,
   38205,
   38204,
   38203,
   38202,
   38201,
   38200,
   38148,
   38152,
   38199,
   38198,
   38197,
   38196,
   38195,
   38194,
   38193,
   38192,
   38191,
   38190,
   38189,
   38188,
   38187,
   38186,
   38185,
   38184,
   38183,
   38182,
   38181,
   38180,
   38179,
   38178,
   38177,
   38176,
 

## Step 3 - Pareto Front identification

In [78]:
class RoutingProblem(Problem):
    def __init__(self, path_data):
        self.path_data = path_data
        super().__init__(n_var=1, n_obj=N_OBJS, n_constr=0, xl=0, xu=len(path_data) - 1)

    def _evaluate(self, X, out, *args, **kwargs):
        objs = []
        for i in X:
            idx = int(i[0])
            objs.append([self.path_data[idx][obj] for obj in OBJS_NOTIME+OBJS_TIME])
        out["F"] = np.array(objs)

We use the [**NSGA-II: Non-dominated Sorting Genetic Algorithm**](https://pymoo.org/algorithms/moo/nsga2.html) to identify the Pareto front.

In [80]:
%%time

termination = DefaultMultiObjectiveTermination(
    xtol=1e-8,
    cvtol=1e-6,
    ftol=0.0025,
    period=30,
    n_max_gen=1000,
    n_max_evals=100000
)

problem = RoutingProblem(path_data)
algorithm = NSGA2(pop_size=10000)
res = minimize(problem, algorithm, verbose=True, termination=termination)

pareto_front = res.F
pareto_solutions = [path_data[int(idx)] for idx in res.X]

n_gen  |  n_eval  | n_nds  |      eps      |   indicator  
     1 |    10000 |     22 |             - |             -
     2 |    20000 |     60 |  0.000000E+00 |             f
     3 |    30000 |    131 |  0.000000E+00 |             f
     4 |    40000 |    262 |  0.000000E+00 |             f
     5 |    50000 |    500 |  0.000000E+00 |             f
     6 |    60000 |    961 |  0.000000E+00 |             f
     7 |    70000 |   1754 |  0.000000E+00 |             f
     8 |    80000 |   3304 |  0.000000E+00 |             f
     9 |    90000 |   6324 |  0.000000E+00 |             f
    10 |   100000 |  10000 |  0.000000E+00 |             f
CPU times: total: 3min 21s
Wall time: 3min 43s


<timed exec>:15: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)


In [81]:
print(f"Number of solutions in pareto front: {len(pareto_solutions)}")

Number of solutions in pareto front: 10000


In [82]:
pareto_solutions

[{'distance': 4788.023428193503,
  'green_area_weight': 3425.8188377378833,
  'pm25_per_meter': 78887.22478814839,
  'path': [3925,
   3911,
   2912,
   2955,
   2919,
   2971,
   26215,
   26217,
   8506,
   8503,
   8502,
   8504,
   26218,
   26216,
   8500,
   8501,
   8505,
   12445,
   12431,
   12436,
   17633,
   12439,
   12437,
   12407,
   12440,
   12450,
   34468,
   34456,
   34478,
   34475,
   34470,
   34469,
   34473,
   34481,
   34459,
   34458,
   34471,
   34462,
   34455,
   34465,
   34454,
   34466,
   34476,
   34482,
   34467,
   34461,
   34480,
   34483,
   34486,
   34463,
   38212,
   38211,
   38210,
   38209,
   38208,
   38207,
   38206,
   38205,
   38204,
   38203,
   38202,
   38201,
   38200,
   38148,
   38152,
   38199,
   38198,
   38197,
   38196,
   38195,
   38194,
   38193,
   38192,
   38191,
   38190,
   38189,
   38188,
   38187,
   38186,
   38185,
   38184,
   38183,
   38182,
   38181,
   38180,
   38179,
   38178,
   38177,
   38176,


### Visualize the first path in the list on a map

In [83]:
def get_coordinates(path):
    coordinates = []
    for node in path:
        n = G.nodes[node]
        coordinates.append([n['lat'], n['lon']])
    return coordinates

In [84]:
for p_sol in pareto_solutions:
    
    coordinates = get_coordinates(p_sol['path'])
    
    m = fo.Map(location=[coordinates[0][0], coordinates[0][1]], zoom_start=13)
    fo.PolyLine(coordinates, color="green", weight=3).add_to(m)
    m.save("map.html")
    break

In [ ]:
%matplotlib inline

x = pareto_front[:, 0]  # first objective
y = pareto_front[:, 1]  # second objective
z = pareto_front[:, 2]  # third objective

fig = plt.figure(figsize=(10, 8))
ax = fig.add_subplot(111, projection='3d')

scatter = ax.scatter(x, y, z, cmap='viridis', marker='o')

ax.set_xlabel('First objective')
ax.set_ylabel('Second objective')
ax.set_zlabel('Third objective')

plt.title('Plot 3D dei dati')
plt.show()

C:\Users\feder\AppData\Local\Temp\ipykernel_35256\1643816156.py:12: UserWarning: No data for colormapping provided via 'c'. Parameters 'cmap' will be ignored
  scatter = ax.scatter(x, y, z, cmap='viridis', marker='o')


In [ ]:
def normalize_objectives(F):
    F_min = F.min(axis=0)
    F_max = F.max(axis=0)
    return (F - F_min) / (F_max - F_min + 1e-9), F_min, F_max


def calculate_normalized_hypervolume(F, ref_point=None, verbose=True):
    F_norm, F_min, F_max = normalize_objectives(F)

    if ref_point is None:
        ref_point = np.ones(F.shape[1]) * 1.1

    hv = HV(ref_point=ref_point)
    hv_value = hv.do(F_norm)

    print(f"Normalized hypervolume: {hv_value:.6f}")
    print(f"Ref point: {ref_point}")

    return hv_value, F_norm


def plot_normalized_pareto(F_norm):

    if F_norm.shape[1] == 2:
        plt.scatter(F_norm[:, 0], F_norm[:, 1])
        plt.xlabel("Objective 1 (normalized)")
        plt.ylabel("Objective 2 (normalized)")
    elif F_norm.shape[1] == 3:
        fig = plt.figure()
        ax = fig.add_subplot(111, projection='3d')
        ax.scatter(F_norm[:, 0], F_norm[:, 1], F_norm[:, 2])
        ax.set_xlabel("Objective 1 (normalized)")
        ax.set_ylabel("Objective 2 (normalized)")
        ax.set_zlabel("Objective 3 (normalized)")
    else:
        print("Plot only for 2 or 3 objectives.")
        return
    plt.title("Normalized Pareto Front")
    plt.grid(True)
    plt.show()

In [ ]:
hv_value, F_norm = calculate_normalized_hypervolume(res.F)
plot_normalized_pareto(F_norm)

In [ ]:
F_norm

## Step 4 - Optimal path selection and interactive exploration

### 4.1 Find the best solution based on user preferences

In [ ]:
OBJS_NOTIME

In [ ]:
OBJS_TIME

In [ ]:
USER_PREF =[0.5, 0.25, 0.25]

In [ ]:
weights = np.array(USER_PREF)
score = (F_norm * weights).sum(axis=1)
best_idx = score.argmin()

In [ ]:
best_idx

In [ ]:
pareto_solutions[best_idx]

In [ ]:
coordinates = get_coordinates(pareto_solutions[best_idx]['path'])

m = fo.Map(location=[coordinates[0][0], coordinates[0][1]], zoom_start=13)
fo.PolyLine(coordinates, color="green", weight=3).add_to(m)
m.save("best_path_user_preferences.html")
break

### 4.2 Find the solution with the optimal trade-off (points closest to the center of pareto front)

In [ ]:
from numpy.linalg import norm

distances = norm(F_norm, axis=1)
best_idx = distances.argmin()

In [ ]:
pareto_solutions[best_idx]

In [ ]:
coordinates = get_coordinates(pareto_solutions[best_idx]['path'])

m = fo.Map(location=[coordinates[0][0], coordinates[0][1]], zoom_start=13)
fo.PolyLine(coordinates, color="green", weight=3).add_to(m)
m.save("optimal_trade_off.html")
break

### 4.3 Find the best solution based on constraints